# Data Warehousing Final Project: *New York this week*

We are going to use the data available from New York's city open data portal (https://data.cityofnewyork.us/) to give in overview of city'status

In [30]:
#set up the Python connector

In [35]:
from __future__ import print_function
import mysql.connector
from mysql.connector import errorcode

In [36]:
try:
 cnx = mysql.connector.connect(user='kristin',
                               password = 'password',
                               database='nyc311',
                              host='0.0.0.0')
except mysql.connector.Error as err:
 if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
   print("Something is wrong with your user name or password")
 elif err.errno == errorcode.ER_BAD_DB_ERROR:
   print("Database does not exist")
 else:
   print(err)
else:
 cnx.close()

config = {
 'user': 'kristin',
 'password': 'password',
 'host': '0.0.0.0',
 'database': 'nyc311',
 'raise_on_warnings': True
}

In [37]:
import requests
import pandas as pd
from datetime import datetime

In order to connect with the API we first need to identify ourselves

In [38]:
with open("app_token.txt") as file: app_token = file.readline().rstrip()

## [311 Service Requests](https://data.cityofnewyork.us/Social-Services/311-Service-Requests-from-2010-to-Present/erm2-nwe9)

In [39]:
# HTTS address to access the 311 data
url = "https://data.cityofnewyork.us/resource/erm2-nwe9.json?"

Reading the [documentation](https://dev.socrata.com/foundry/data.cityofnewyork.us/erm2-nwe9) of the API, we see that we can introduce SQL querries

In [40]:
querry = "$where=created_date between '2019-11-01T00:00:00' and '2019-11-07T00:00:00'&$limit=1000"

### Example: Get the 311 calls between Nov 1st 2019, and Nov 8th 2019

In [41]:
querry_url = url + "$$app_token=" + app_token + "&" + querry
querry_url

"https://data.cityofnewyork.us/resource/erm2-nwe9.json?$$app_token=x1uqIJMOnjOzlZZUrIcEwUY40&$where=created_date between '2019-11-01T00:00:00' and '2019-11-07T00:00:00'&$limit=1000"

In [42]:
response = requests.get(querry_url)

In [43]:
calls = response.json()

In [44]:
len(calls)

1000

In [45]:
calls

[{'unique_key': '44197263',
  'created_date': '2019-11-01T00:00:01.000',
  'agency': 'NYPD',
  'agency_name': 'New York City Police Department',
  'complaint_type': 'Blocked Driveway',
  'descriptor': 'No Access',
  'location_type': 'Street/Sidewalk',
  'incident_zip': '10305',
  'incident_address': '167 LACONIA AVENUE',
  'street_name': 'LACONIA AVENUE',
  'cross_street_1': 'BENTON AVENUE',
  'cross_street_2': 'EVERGREEN AVENUE',
  'intersection_street_1': 'BENTON AVENUE',
  'intersection_street_2': 'EVERGREEN AVENUE',
  'city': 'STATEN ISLAND',
  'landmark': 'LACONIA AVENUE',
  'status': 'In Progress',
  'community_board': '02 STATEN ISLAND',
  'bbl': '5033590043',
  'borough': 'STATEN ISLAND',
  'x_coordinate_state_plane': '960399',
  'y_coordinate_state_plane': '154612',
  'open_data_channel_type': 'PHONE',
  'park_facility_name': 'Unspecified',
  'park_borough': 'STATEN ISLAND',
  'latitude': '40.591018313006884',
  'longitude': '-74.08587711831751',
  'location': {'latitude': '40

In [46]:
#Transform the lists of dictionaries obtained into a Pandas DataFrame
results_df = pd.DataFrame.from_records(calls)

In [47]:
results_df.head()

address_type agency                                        agency_name  \
0          NaN   NYPD                    New York City Police Department   
1      ADDRESS    HPD  Department of Housing Preservation and Develop...   
2          NaN   NYPD                    New York City Police Department   
3          NaN   NYPD                    New York City Police Department   
4          NaN   NYPD                    New York City Police Department   

          bbl        borough bridge_highway_direction bridge_highway_segment  \
0  5033590043  STATEN ISLAND                      NaN                    NaN   
1  3018120025       BROOKLYN                      NaN                    NaN   
2  3052090033       BROOKLYN                      NaN                    NaN   
3  1021740103      MANHATTAN                      NaN                    NaN   
4  4034810062         QUEENS                      NaN                    NaN   

            city              closed_date   community_board  ...  \
0  STATEN ISLAND                      NaN  02 STATEN ISLAND  ...   
1       BROOKLYN  2019-11-02T02:12:38.000       03 BROOKLYN  ...   
2       BROOKLYN  2019-11-01T01:37:55.000       14 BROOKLYN  ...   
3       NEW YORK  2019-11-01T01:51:21.000      12 MANHATTAN  ...   
4      RIDGEWOOD  2019-11-01T03:21:27.000         05 QUEENS  ...   

                              resolution_description road_ramp       status  \
0                                                NaN       NaN  In Progress   
1  The Department of Housing Preservation and Dev...       NaN       Closed   
2  The Police Department responded to the complai...       NaN       Closed   
3  The Police Department responded to the complai...       NaN       Closed   
4  The Police Department responded to the complai...       NaN       Closed   

        street_name taxi_company_borough taxi_pick_up_location unique_key  \
0    LACONIA AVENUE                  NaN                   NaN   44197263   
1      GATES AVENUE                  NaN                   NaN   44199138   
2  EAST   23 STREET                  NaN                   NaN   44198245   
3    ELLWOOD STREET                  NaN                   NaN   44196453   
4     PUTNAM AVENUE                  NaN                   NaN   44199219   

  vehicle_type x_coordinate_state_plane y_coordinate_state_plane  
0          NaN                   960399                   154612  
1          NaN                   997361                   189196  
2          NaN                   996435                   172373  
3          NaN                  1004027                   252748  
4          NaN                  1011112                   195708  

[5 rows x 39 columns]

In [55]:
# Create a sql table

config = {
 'user': 'kristin',
 'password': 'password',
 'host': '0.0.0.0',
 'database': 'nyc311',
 'raise_on_warnings': True
}

DB_NAME = 'nyc311'
TABLES = {}
TABLES['complaints'] = (
   "CREATE TABLE complaints ("
   "  address_type varchar(10),"
   "  agency varchar(10),"
   "  agency_name varchar(20),"
   "  borough varchar(20),"
   "  closed_date date,"
   "  unique_key integer NOT NULL,"
   "  PRIMARY KEY (unique_key)"
   ") ENGINE=InnoDB")

cnx = mysql.connector.connect(**config)
cursor = cnx.cursor()
for table_name in TABLES:
   table_description = TABLES[table_name]
   try:
       print("Creating table {}: ".format(table_name), end='')
       cursor.execute(table_description)
   except mysql.connector.Error as err:
       if err.errno == errorcode.ER_TABLE_EXISTS_ERROR:
           print("already exists.")
       else:
           print(err.msg)
   else:
       print("OK")
cursor.close()
cnx.close()

Creating table complaints: already exists.


In [57]:
# Insert data into the table

cnx = mysql.connector.connect(**config)
cursor = cnx.cursor()
calls_sql = (
  "insert into calls3"
  "(unique_key,address_type,agency,agency_name, borough, closed_date,status)"
  "values (%(unique_key)s, %(address_type)s, %(agency)s, %(agency_name)s, %(borough)s, %(closed_date)s,%(status)s)")
for call in dict_you_want:
  cursor.execute(calls_sql, call)
cnx.commit()
cursor.close()
cnx.close()

NameError: name 'dict_you_want' is not defined

### Top types of complaints

In [92]:
results_df["complaint_type"].value_counts()[0:10]

HEAT/HOT WATER                7426
Noise - Residential           3935
Illegal Parking               3419
Blocked Driveway              2427
Noise - Street/Sidewalk       1251
Street Light Condition        1159
For Hire Vehicle Complaint    1143
Damaged Tree                  1087
Noise                          933
Street Condition               885
Name: complaint_type, dtype: int64

### Most complaint agencies

In [95]:
results_df["agency_name"].value_counts()[0:10]

New York City Police Department                       13769
Department of Housing Preservation and Development     9769
Department of Transportation                           3854
Department of Environmental Protection                 2317
Department of Parks and Recreation                     2226
Taxi and Limousine Commission                          1568
Department of Buildings                                1508
Department of Health and Mental Hygiene                 862
Department of Homeless Services                         539
BCC - Brooklyn South                                    264
Name: agency_name, dtype: int64

### Dealing with dates

In [98]:
results_df.created_date

0        2019-11-01T00:00:01.000
1        2019-11-01T00:00:03.000
2        2019-11-01T00:00:03.000
3        2019-11-01T00:00:35.000
4        2019-11-01T00:00:43.000
                  ...           
38350    2019-11-06T23:59:48.000
38351    2019-11-06T23:59:49.000
38352    2019-11-06T23:59:49.000
38353    2019-11-06T23:59:51.000
38354    2019-11-06T23:59:53.000
Name: created_date, Length: 38355, dtype: object

We need to transform dates into a python date type

In [110]:
date1 = results_df.created_date[0]
date1

'2019-11-01T00:00:01.000'

In [111]:
date_trans = datetime.strptime(date1, "%Y-%m-%dT%H:%M:%S.%f" )
print(date_trans)

2019-11-01 00:00:01


In [117]:
date_trans.year

2019

In [119]:
pd.to_datetime(results_df.created_date, format = "%Y-%m-%dT%H:%M:%S.%f")

0       2019-11-01 00:00:01
1       2019-11-01 00:00:03
2       2019-11-01 00:00:03
3       2019-11-01 00:00:35
4       2019-11-01 00:00:43
                ...        
38350   2019-11-06 23:59:48
38351   2019-11-06 23:59:49
38352   2019-11-06 23:59:49
38353   2019-11-06 23:59:51
38354   2019-11-06 23:59:53
Name: created_date, Length: 38355, dtype: datetime64[ns]

In [120]:
results_df.created_date = pd.to_datetime(results_df.created_date, format = "%Y-%m-%dT%H:%M:%S.%f")

In [122]:
results_df.closed_date = pd.to_datetime(results_df.closed_date, format = "%Y-%m-%dT%H:%M:%S.%f")

## [Events information](https://data.cityofnewyork.us/City-Government/NYC-Permitted-Event-Information/tvpp-9vvx)

In [142]:
url = "https://data.cityofnewyork.us/resource/tvpp-9vvx.json?"

In [143]:
querry = "$where=start_date_time > '2019-01-01T00:00:00'&$limit=50000"

In [153]:
response = requests.get(url + "$$app_token=" + app_token + "&" + querry)

In [154]:
events = response.json()

In [155]:
events

[{'event_id': '429352',
  'event_name': 'Down to Earth Chelsea Farmers Market',
  'start_date_time': '2019-11-09T07:00:00.000',
  'end_date_time': '2019-11-09T18:00:00.000',
  'event_agency': 'Street Activity Permit Office',
  'event_type': 'Farmers Market',
  'event_borough': 'Manhattan',
  'event_location': ' WEST   23 STREET between 8 AVENUE and 9 AVENUE',
  'event_street_side': 'North',
  'street_closure_type': 'Partial Sidewalk Closure ',
  'community_board': '4, ',
  'police_precinct': '10, '},
 {'event_id': '429352',
  'event_name': 'Down to Earth Chelsea Farmers Market',
  'start_date_time': '2019-11-16T07:00:00.000',
  'end_date_time': '2019-11-16T18:00:00.000',
  'event_agency': 'Street Activity Permit Office',
  'event_type': 'Farmers Market',
  'event_borough': 'Manhattan',
  'event_location': ' WEST   23 STREET between 8 AVENUE and 9 AVENUE',
  'event_street_side': 'North',
  'street_closure_type': 'Partial Sidewalk Closure ',
  'community_board': '4, ',
  'police_precinct

In [156]:
events = pd.DataFrame(events)
events

event_id                                      event_name  \
0       429352            Down to Earth Chelsea Farmers Market   
1       429352            Down to Earth Chelsea Farmers Market   
2       429352            Down to Earth Chelsea Farmers Market   
3       429352            Down to Earth Chelsea Farmers Market   
4       429352            Down to Earth Chelsea Farmers Market   
...        ...                                             ...   
10819   515434                              Soccer -Regulation   
10820   515536  Thanksgiving Day Parade of Unity and Diversity   
10821   515537                            Permitted Film Event   
10822   515636                        Shipping Naming Ceremony   
10823   515656                                Press Conference   

               start_date_time            end_date_time  \
0      2019-11-09T07:00:00.000  2019-11-09T18:00:00.000   
1      2019-11-16T07:00:00.000  2019-11-16T18:00:00.000   
2      2019-11-23T07:00:00.000  2019-11-23T18:00:00.000   
3      2019-11-30T07:00:00.000  2019-11-30T18:00:00.000   
4      2019-12-07T07:00:00.000  2019-12-07T18:00:00.000   
...                        ...                      ...   
10819  2019-11-12T15:00:00.000  2019-11-12T18:00:00.000   
10820  2019-11-27T09:00:00.000  2019-11-27T11:00:00.000   
10821  2019-11-08T06:00:00.000  2019-12-07T22:00:00.000   
10822  2019-11-12T13:00:00.000  2019-11-12T14:00:00.000   
10823  2019-11-18T10:00:00.000  2019-11-18T11:30:00.000   

                                         event_agency  \
0                       Street Activity Permit Office   
1                       Street Activity Permit Office   
2                       Street Activity Permit Office   
3                       Street Activity Permit Office   
4                       Street Activity Permit Office   
...                                               ...   
10819                                Parks Department   
10820                               Police Department   
10821  Mayor's Office of Film, Theatre & Broadcasting   
10822                                Parks Department   
10823                                Parks Department   

                           event_type event_borough  \
0                      Farmers Market     Manhattan   
1                      Farmers Market     Manhattan   
2                      Farmers Market     Manhattan   
3                      Farmers Market     Manhattan   
4                      Farmers Market     Manhattan   
...                               ...           ...   
10819                   Sport - Youth         Bronx   
10820                          Parade        Queens   
10821  Theater Load in and Load Outs      Manhattan   
10822                   Special Event     Manhattan   
10823                   Special Event     Manhattan   

                                          event_location event_street_side  \
0         WEST   23 STREET between 8 AVENUE and 9 AVENUE             North   
1         WEST   23 STREET between 8 AVENUE and 9 AVENUE             North   
2         WEST   23 STREET between 8 AVENUE and 9 AVENUE             North   
3         WEST   23 STREET between 8 AVENUE and 9 AVENUE             North   
4         WEST   23 STREET between 8 AVENUE and 9 AVENUE             North   
...                                                  ...               ...   
10819                         Starlight Park: Soccer-01                NaN   
10820   67 DRIVE between 79 STREET and 80 STREET,  80...              Full   
10821          Broadhurst Theatre: 235 West 44th Street                NaN   
10822                           Battery Park: Promenade                NaN   
10823  Thomas Paine Park (Foley Square): Thomas Paine...               NaN   

             street_closure_type community_board police_precinct  
0      Partial Sidewalk Closure              4,             10,   
1      Partial Sidewalk Closure              4,             10,   
2      Partial Sidew

## [DHS Daily Report - Homelesness](https://data.cityofnewyork.us/Social-Services/DHS-Daily-Report/k46n-sa2m)

In [160]:
url = "https://data.cityofnewyork.us/resource/k46n-sa2m.json?"

In [165]:
response = requests.get(url + "$$app_token=" + app_token + "&$limit=50000")

In [166]:
dhs = response.json()

In [167]:
dhs

[{'date_of_census': '2019-11-06T00:00:00.000',
  'total_adults_in_shelter': '38312',
  'total_children_in_shelter': '21809',
  'total_individuals_in_shelter': '60121',
  'single_adult_men_in_shelter': '12059',
  'single_adult_women_in_shelter': '4544',
  'total_single_adults_in_shelter': '16603',
  'families_with_children_in_shelter': '12223',
  'adults_in_families_with_children_in_shelter': '16356',
  'children_in_families_with_children_in_shelter': '21809',
  'total_individuals_in_families_with_children_in_shelter_': '38165',
  'adult_families_in_shelter': '2537',
  'individuals_in_adult_families_in_shelter': '5353'},
 {'date_of_census': '2019-11-05T00:00:00.000',
  'total_adults_in_shelter': '38233',
  'total_children_in_shelter': '21750',
  'total_individuals_in_shelter': '59983',
  'single_adult_men_in_shelter': '12061',
  'single_adult_women_in_shelter': '4525',
  'total_single_adults_in_shelter': '16586',
  'families_with_children_in_shelter': '12196',
  'adults_in_families_with

In [168]:
dhs = pd.DataFrame(dhs)
dhs

date_of_census total_adults_in_shelter  \
0     2019-11-06T00:00:00.000                   38312   
1     2019-11-05T00:00:00.000                   38233   
2     2019-11-04T00:00:00.000                   38221   
3     2019-11-03T00:00:00.000                   38235   
4     2019-11-02T00:00:00.000                   38084   
...                       ...                     ...   
2201  2013-08-25T00:00:00.000                   28458   
2202  2013-08-24T00:00:00.000                   28274   
2203  2013-08-23T00:00:00.000                   28257   
2204  2013-08-22T00:00:00.000                   28366   
2205  2013-08-21T00:00:00.000                   28359   

     total_children_in_shelter total_individuals_in_shelter  \
0                        21809                        60121   
1                        21750                        59983   
2                        21730                        59951   
3                        21743                        59978   
4                        21725                        59809   
...                        ...                          ...   
2201                     21400                        49858   
2202                     21343                        49617   
2203                     21291                        49548   
2204                     21324                        49690   
2205                     21314                        49673   

     single_adult_men_in_shelter single_adult_women_in_shelter  \
0                          12059                          4544   
1                          12061                          4525   
2                          12044                          4504   
3                          12018                          4529   
4                          11920                          4526   
...                          ...                           ...   
2201                        7230                          2704   
2202                        7110                          2690   
2203                        7149                          2671   
2204                        7201                          2716   
2205                        7231                          2710   

     total_single_adults_in_shelter families_with_children_in_shelter  \
0                             16603                             12223   
1                             16586                             12196   
2                             16548                             12192   
3                             16547                             12207   
4                             16446                             12194   
...                             ...                               ...   
2201                           9934                             10324   
2202                           9800                             10291   
2203                           9820                             10266   
2204                           9917                             10274   
2205                           9941                             10261   

     adults_in_families_with_children_in_shelter  \
0                                          16356   
1                                          16326   
2                                          16322   
3                                          16349   
4                                          16335   
...                                          ...   
2201                                       14694   
2202                                       14650   
2203                                       14611   
2204                                       14622   
2205                                       14607   

     children_in_families_with_children_in_shelter  \
0                                            21809   
1                                            21750   
2                                            21730   
3                                            21743   
4       

## [Accidents](https://data.cityofnewyork.us/Public-Safety/Motor-Vehicle-Collisions-Crashes/h9gi-nx95)

In [177]:
url = "https://data.cityofnewyork.us/resource/h9gi-nx95.json?"

In [186]:
querry = "$where=date > '2019-01-01T00:00:00'&$limit=50000"

In [187]:
response = requests.get(url + "$$app_token=" + app_token + "&" + querry)

In [205]:
acc = response.json()

In [206]:
acc

[{'date': '2019-01-02T00:00:00.000',
  'time': '17:00',
  'latitude': '40.7399500',
  'longitude': '-73.8455300',
  'location': {'type': 'Point', 'coordinates': [-73.84553, 40.73995]},
  'on_street_name': 'LONG ISLAND EXPRESSWAY          ',
  'off_street_name': 'GRAND CENTRAL PARKWAY',
  'number_of_persons_injured': '0',
  'number_of_persons_killed': '0',
  'number_of_pedestrians_injured': '0',
  'number_of_pedestrians_killed': '0',
  'number_of_cyclist_injured': '0',
  'number_of_cyclist_killed': '0',
  'number_of_motorist_injured': '0',
  'number_of_motorist_killed': '0',
  'contributing_factor_vehicle_1': 'Unspecified',
  'contributing_factor_vehicle_2': 'Unspecified',
  'collision_id': '4061228',
  'vehicle_type_code1': 'Sedan',
  'vehicle_type_code2': 'Station Wagon/Sport Utility Vehicle'},
 {'date': '2019-01-02T00:00:00.000',
  'time': '22:10',
  'borough': 'QUEENS',
  'zip_code': '11367',
  'latitude': '40.7260480',
  'longitude': '-73.8240050',
  'location': {'type': 'Point', '

In [207]:
acc = pd.DataFrame(acc)
acc

date   time    latitude    longitude  \
0      2019-01-02T00:00:00.000  17:00  40.7399500  -73.8455300   
1      2019-01-02T00:00:00.000  22:10  40.7260480  -73.8240050   
2      2019-01-02T00:00:00.000   1:43  40.6945570  -73.9432500   
3      2019-01-02T00:00:00.000   8:15  40.7071900  -73.9151100   
4      2019-01-02T00:00:00.000   8:50  40.6632270  -73.9315900   
...                        ...    ...         ...          ...   
49995  2019-03-31T00:00:00.000  14:00  40.5870170  -73.9629750   
49996  2019-03-31T00:00:00.000  19:05  40.5837020  -73.9694600   
49997  2019-03-31T00:00:00.000   9:00  40.6453970  -73.9189300   
49998  2019-03-31T00:00:00.000  22:15  40.6879500  -73.8250200   
49999  2019-03-31T00:00:00.000   0:59  40.7283940  -74.0031360   

                                                location  \
0      {'type': 'Point', 'coordinates': [-73.84553, 4...   
1      {'type': 'Point', 'coordinates': [-73.824005, ...   
2      {'type': 'Point', 'coordinates': [-73.94325, 4...   
3      {'type': 'Point', 'coordinates': [-73.91511, 4...   
4      {'type': 'Point', 'coordinates': [-73.93159, 4...   
...                                                  ...   
49995  {'type': 'Point', 'coordinates': [-73.962975, ...   
49996  {'type': 'Point', 'coordinates': [-73.96946, 4...   
49997  {'type': 'Point', 'coordinates': [-73.91893, 4...   
49998  {'type': 'Point', 'coordinates': [-73.82502, 4...   
49999  {'type': 'Point', 'coordinates': [-74.003136, ...   

                         on_street_name         off_street_name  \
0      LONG ISLAND EXPRESSWAY             GRAND CENTRAL PARKWAY   
1      72 AVENUE                                     141 STREET   
2      THROOP AVENUE                                        NaN   
3      SENECA AVENUE                           STOCKHOLM STREET   
4      UTICA AVENUE                        EAST NEW YORK AVENUE   
...                                 ...                     ...   
49995  AVENUE Z                                  HUBBARD STREET   
49996  BELT PARKWAY                                         NaN   
49997  BRANTON STREET                             DITMAS AVENUE   
49998  LEFFERTS BOULEVARD                            103 AVENUE   
49999  BEDFORD STREET                    AVENUE OF THE AMERICAS   

      number_of_persons_injured number_of_persons_killed  \
0                             0                        0   
1                             0                        0   
2                             0                        0   
3                             0                        0   
4                             0                        0   
...                         ...                      ...   
49995                         0                        0   
49996                         0                        0   
49997                         0                        0   
49998                         0                        0   
49999                         1                        0   

      number_of_pedestrians_injured  ...                   vehicle_type_code2  \
0                                 0  ...  Station Wagon/Sport Utility Vehicle   
1                                 0  ...  Station Wagon/Sport Utility Vehicle   
2                                 0  ...                                  NaN   
3                                 0  ...  Station Wagon/Sport Utility Vehicle   
4                                 0  ...                                Sedan   
...                             ...  ...                                  ...   
49995                             0  ...  Station Wagon/Sport Utility Vehicle   
49996                             0  ...                                Sedan   
49997                             0  ...                                  NaN   
49998                             0  ...                                Sedan   
49999                             0  ...                                  NaN   

         boro

In [208]:
acc.number_of_persons_injured

0        0
1        0
2        0
3        0
4        0
        ..
49995    0
49996    0
49997    0
49998    0
49999    1
Name: number_of_persons_injured, Length: 50000, dtype: object

In [209]:
acc.number_of_persons_injured = pd.to_numeric(acc.number_of_persons_injured)  

In [211]:
acc.number_of_persons_injured

0        0
1        0
2        0
3        0
4        0
        ..
49995    0
49996    0
49997    0
49998    0
49999    1
Name: number_of_persons_injured, Length: 50000, dtype: int64

In [212]:
acc[["borough", "number_of_persons_injured"]].groupby(["borough"]).sum()

number_of_persons_injured
borough                                 
BRONX                               1395
BROOKLYN                            2745
MANHATTAN                           1119
QUEENS                              2369
STATEN ISLAND                        329

In [213]:
acc.number_of_persons_injured.sum()

13009

Relevant documentation

* [Filtering dates](https://dev.socrata.com/docs/datatypes/floating_timestamp.html#)
* [SQL querries](https://dev.socrata.com/docs/queries/)